In [1]:
import matplotlib.pyplot as plt
import matplotlib.tri as mtri
import numpy as np

In [2]:
from algorithms.meshforrectangle import MeshForRectangle

In [3]:
rectangle = [[0,0],[0,2],[1,2],[1,0]]
rectangle_area = 2
u = lambda x, y: (x - 1)**2 * (y - 2)**2 *x*y
a11 = 1
a22 = 1
f = lambda x, y: 2 * x * (x - 1)**2 * (3*y - 4) + 2*(3*x - 2)*(y - 2)**2 * y
f(13, 99)

70027326

$$
Input interpretation:
\frac{\partial^{2}\left((x-1)^{2}(y-2)^{2} x y\right)}{\partial x^{2}}+\frac{\partial^{2}\left((x-1)^{2}(y-2)^{2} x y\right)}{\partial y^{2}}
$$
$$
Result:
2 x(x-1)^{2}(3 y-4)+2(3 x-2)(y-2)^{2} y
$$

---
##### (d^2/dx^2  (x - 1)^2 * (y - 2)^2) + (d^2/dy^2 (x - 1)^2 * (y - 2)^2) )

In [4]:
nx = 100
ny = 100
mesher = MeshForRectangle(nx, ny)
triangulation = list(map(lambda t: t.get_points(), mesher.triangulate(rectangle)))

In [5]:
points = np.unique(np.concatenate(triangulation), axis=0).tolist()
triangles = list(map(lambda tri: [points.index(tri[0]),
                                  points.index(tri[1]),
                                  points.index(tri[2]),], triangulation))

In [6]:



#  def get_numeration_vertcies(triangulation):
#     points = {}

#     count = 1

#     for tr in triangulation:
#         if tr.p1 not in points.values():
#             points.update({count: tr.p1})
#             count += 1

#         if tr.p2 not in points.values():
#             points.update({count: tr.p2})
#             count += 1

#         if tr.p3 not in points.values():
#             points.update({count: tr.p3})
#             count += 1
#     return points

# res = get_numeration_vertcies(mesher.triangulate(rectangle))
# [print(el.get_coords()) for el in res.values()]

In [7]:
x, y = [l.ravel() for l in np.split(points, [-1], axis=1)]

triang = mtri.Triangulation(x, y, triangles)

# Interpolate to regularly-spaced quad grid.
z = u(x,y)

xi, yi = np.meshgrid(np.linspace(0, 3, 20), np.linspace(0, 3, 20))

# Set up the figure
fig, ax = plt.subplots(figsize=(nx,ny))#plt.subplots(nrows=2, ncols=2)

plt.xlim(0, 2.5)
plt.ylim(0, 2.5)

# Plot the triangulation.
ax.tricontourf(triang, z)
ax.triplot(triang, 'ko-')
ax.set_title('Triangular grid')

fig.tight_layout()
plt.show()

In [8]:
def K_i(b, c, s, a11, a22):
    K = np.zeros([3, 3])
    for i in range(3):
        for j in range(3):
            K[i][j] = a11 * (b[i] * b[j]) + a22 * (c[i] * c[j])
    K /= 4 * s
    return K


def fill_A_with_K_i(A, K, tri):
    for i in range(3):
        for j in range(3):
            A[tri[i]][tri[j]] += K[i][j]
            
def fill_F_with_phi_i(F, phi, tri, points=points):    
    for i, (p_i, phi_i) in enumerate(zip(tri, phi)):
        F[p_i] += phi_i * f(*points[p_i])

In [9]:
n =  len(triangles)

triangle_area = rectangle_area / n
s = triangle_area / 3


a = np.zeros([n, 3])
b = np.zeros([n, 3])
c = np.zeros([n, 3])
phi = np.zeros([n, 3])
dN_x1 = np.zeros([n, 3])
dN_x2 = np.zeros([n, 3])

print("a: ", a.shape)
print("b: ", a.shape)
print("c: ", a.shape)

delta = 2 * s * 3

K = np.zeros([n, 3, 3])
A = np.zeros([len(points), len(points)])
F = np.zeros([len(points), 1])

for i, tri in enumerate(triangles):
    p1 = points[tri[0]]
    p2 = points[tri[1]] 
    p3 = points[tri[2]]
    p = [(p1[0] + p2[0] + p3[0])/3, (p1[1] + p2[1] + p3[1])/3] 
    
    groups = [
        (p2, p3, _), (p3, p1, _), (p2, p1, _)
    ]
    
    for j, group in enumerate(groups):
        t1 = group[0]
        t2 = group[1]
        t3 = group[2]
        
        a[i][j] = t1[0] * t2[1] - t2[0] * t1[1]
        b[i][j] = t1[1] - t2[1]
        c[i][j] = t2[0] - t1[0]
        
        dN_x1[i][j] = 1/delta * b[i][j]
        dN_x2[i][j] = 1/delta * c[i][j]

        #phi[i][j] = 1/3
        phi[i][j] = (a[i][j] + b[i][j] * p[0] + c[i][j] * p[1]) / delta

    K[i] = K_i(b[i], c[i], s, a11, a22)
    fill_A_with_K_i(A, K[i], tri)
    fill_F_with_phi_i(F, phi[i], tri)

phi

a:  (20000, 3)
b:  (20000, 3)
c:  (20000, 3)


array([[ 0.33333333,  0.33333333, -0.33333333],
       [ 0.33333333,  0.33333333, -0.33333333],
       [ 0.33333333,  0.33333333, -0.33333333],
       ...,
       [ 0.33333333,  0.33333333, -0.33333333],
       [ 0.33333333,  0.33333333, -0.33333333],
       [ 0.33333333,  0.33333333, -0.33333333]])

In [10]:
import numpy.linalg as LA
b = LA.solve(A, F)

In [11]:
ex = [u(*p) for p in points]
np.max(b - ex)


0.08779486419764783

In [12]:


for l in range(n):
    for i in range(3):
        for j in range(3):
            

SyntaxError: unexpected EOF while parsing (<ipython-input-12-90243038410e>, line 4)